In [1]:
import tushare as ts
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import MySQLdb
import time
import datetime
import warnings
warnings.filterwarnings("ignore")
from imp import reload
import chan_series

In [2]:
db = MySQLdb.connect(host="127.0.0.1",user="sa",passwd="sasasa",db="quant",charset="utf8")
cursor = db.cursor()
sql = "select * from stock_min where ts_code='000338.SZ' and trade_time>'2010-01-01' and trade_time<'2020-01-01' order by trade_time"
df = pd.read_sql(sql,db)
cursor.close()
db.close()
print('data loaded',len(df))
reload(chan_series) #重新加载外部chan.py
df=chan_series.build(df)

data loaded 578535
开始处理： 0 / 578535
开始处理： 10000 / 578535
开始处理： 20000 / 578535
开始处理： 30000 / 578535
开始处理： 40000 / 578535
开始处理： 50000 / 578535
开始处理： 60000 / 578535
开始处理： 70000 / 578535
开始处理： 80000 / 578535
开始处理： 90000 / 578535
开始处理： 100000 / 578535
开始处理： 110000 / 578535
开始处理： 120000 / 578535
开始处理： 130000 / 578535
开始处理： 140000 / 578535
开始处理： 150000 / 578535
开始处理： 160000 / 578535
开始处理： 170000 / 578535
开始处理： 180000 / 578535
开始处理： 190000 / 578535
开始处理： 200000 / 578535
开始处理： 210000 / 578535
开始处理： 220000 / 578535
开始处理： 230000 / 578535
开始处理： 240000 / 578535
开始处理： 250000 / 578535
开始处理： 260000 / 578535
开始处理： 270000 / 578535
开始处理： 280000 / 578535
开始处理： 290000 / 578535
开始处理： 300000 / 578535
开始处理： 310000 / 578535
开始处理： 320000 / 578535
开始处理： 330000 / 578535
开始处理： 340000 / 578535
开始处理： 350000 / 578535
开始处理： 360000 / 578535
开始处理： 370000 / 578535
开始处理： 380000 / 578535
开始处理： 390000 / 578535
开始处理： 400000 / 578535
开始处理： 410000 / 578535
开始处理： 420000 / 578535
开始处理： 430000 / 578535
开始处理： 440000 / 578535
开始处理：

In [4]:
result_df=pd.DataFrame()
qs_mark_df=pd.DataFrame()
zs_no_pre=0
last_zg=0
last_zd=0
last_zsg_gg=0
last_zsg_dd=0
last_zsg_nos=''
last_zsg_dir=''
last_zsg_start_dir=''
last_zsg_end_dir=''
is_merge_last=False
is_buy=False
last_buy_price=0
profit=0
profit_100=100
for n, k in df.loc[(df["line"]=='bottom') | (df["line"]=='top')].iterrows():
    #print(zs_no_pre,k.zs_no,zs_no_pre==0)
    if zs_no_pre!=0 and (k.zs_no==0 or k.zs_no>zs_no_pre): #中枢结束
        #print('中枢结束',zs_no_pre, '合并',is_merge_last)
        last_zsg_end_dir='down' if k.line=='bottom' else 'up'
        #print(last_zsg_start_dir,last_zsg_end_dir,last_zsg_dir,last_zsg_nos)
        if is_merge_last:
            #update last one
            index=len(qs_mark_df)-1
            qs_mark_df.ix[index,'zsg_gg']=last_zsg_gg            
            qs_mark_df.ix[index,'zsg_dd']=last_zsg_dd
            qs_mark_df.ix[index,'zsg_nos']=last_zsg_nos
            qs_mark_df.ix[index,'zsg_end_dir']=last_zsg_end_dir
        else:
            #append to list
            #print(zs_no_pre,k.zs_no)
            qs_mark_df=qs_mark_df.append({'zsg_start_dir':last_zsg_start_dir,'zsg_end_dir':last_zsg_end_dir, 'zsg_dir':last_zsg_dir, 'zsg_gg':last_zsg_gg, 'zsg_dd':last_zsg_dd, 'zsg_nos':last_zsg_nos},ignore_index=True)
        
        last_zs_k=df.loc[0:n].loc[df["zs_no"]>0].iloc[-1] if k.zs_no==0 else df.loc[0:n-1].loc[df["zs_no"]>0].iloc[-1]
        last_zg=last_zs_k.zg
        last_zd=last_zs_k.zd
        #print(last_zs_k.zs_no,last_zg,last_zd)

    if k.zs_no!=0 and (zs_no_pre==0 or k.zs_no>zs_no_pre): #新中枢
        #print('新中枢',k.zs_no,k.zg,k.zd)
        #是否与前面中枢需要合并
        if last_zsg_dd!=0 and last_zsg_gg!=0 and max(last_zsg_dd,k.dd)<min(last_zsg_gg,k.gg):
            #print(last_zsg_gg,last_zsg_dd,k.gg,k.dd)
            last_zsg_gg=max(last_zsg_gg,k.gg)
            last_zsg_dd=min(last_zsg_dd,k.dd)
            last_zsg_nos+=(str(int(k.zs_no))+',')
            is_merge_last=True
        else:
            if last_zsg_dd==0:
                last_zsg_dir=''
            else:
                last_zsg_dir='down' if k.gg<last_zsg_dd else 'up'
            last_zsg_gg=k.gg
            last_zsg_dd=k.dd
            last_zsg_nos=(str(int(k.zs_no))+',')
            last_zsg_start_dir='down' if k.line=='bottom' else 'up'
            is_merge_last=False    
        
#     if is_buy!=True and k.line=='bottom' and len(qs_mark_df)>=2: #找三买
#         k1_dir=qs_mark_df.iloc[-2].zsg_dir
#         k1_start_dir=qs_mark_df.iloc[-2].zsg_start_dir
#         k1_end_dir=qs_mark_df.iloc[-2].zsg_end_dir
#         k2_dir=qs_mark_df.iloc[-1].zsg_dir
#         k2_start_dir=qs_mark_df.iloc[-1].zsg_start_dir
#         k2_end_dir=qs_mark_df.iloc[-1].zsg_end_dir
#         k2_gg=qs_mark_df.iloc[-1].zsg_gg            
#         k2_dd=qs_mark_df.iloc[-1].zsg_dd
#         #print(k1_start_dir,k1_end_dir,k2_start_dir,k2_end_dir,k2_dir)
#         #买点形态
#         is_qs_ok=False
#         if k1_start_dir=='down' and k1_end_dir=='down' and k2_start_dir=='down' and k2_end_dir=='down' and k2_dir=='down':
#             is_qs_ok=True
#         if k1_start_dir=='down' and k1_end_dir=='down' and k2_start_dir=='down' and k2_end_dir=='up' and k2_dir=='down':
#             is_qs_ok=True
#         #print('is_qs_ok')
#         if is_qs_ok and k.low>k2_gg: #没有碰到中枢，反弹
#             print('买入',k.close,k.trade_time, k.line, k2_gg, k2_dd)
#             is_buy=True
#             last_buy_price=k.close

    if is_buy!=True and k.line=='bottom' and len(qs_mark_df)>=2: #找买点
        k2_dir=qs_mark_df.iloc[-1].zsg_dir
        k2_start_dir=qs_mark_df.iloc[-1].zsg_start_dir
        k2_end_dir=qs_mark_df.iloc[-1].zsg_end_dir
        #print(k1_start_dir,k1_end_dir,k2_start_dir,k2_end_dir,k2_dir)
        #买点形态
        if k2_end_dir=='up' and k.low>last_zg: #没有碰到中枢，反弹
            print('买入',k.close,k.trade_time, k.line)
            is_buy=True
            last_buy_price=k.close
            
    if is_buy and k.line=='top' and len(qs_mark_df)>=2: #找卖点
        k2_dir=qs_mark_df.iloc[-1].zsg_dir
        k2_start_dir=qs_mark_df.iloc[-1].zsg_start_dir
        k2_end_dir=qs_mark_df.iloc[-1].zsg_end_dir
        #print(k1_end_dir,k.high,last_zd)
        #卖点形态
        if k2_end_dir=='down' and k.high<last_zd: #没有碰到中枢zd，下反弹
            #一股变几股
            rate=1
            trade_time=k.trade_time.strftime("%Y-%m-%d %H:%M:%S")
            if trade_time=='2015-08-20 10:11:00':
                rate=2
            elif trade_time=='2017-07-21 13:38:00':
                rate=2
            
            profit+=k.close*rate-last_buy_price
            profit_100=profit_100*(k.close*rate/last_buy_price)
            print('卖出',k.close*rate,'本次获利',k.close*rate-last_buy_price,'总获利',profit,k.trade_time,'100初仓累计：',profit_100)
            is_buy=False
                
    zs_no_pre=k.zs_no

买入 68.0 2010-01-06 13:04:00 bottom
卖出 68.54 本次获利 0.5400000000000063 总获利 0.5400000000000063 2010-01-13 11:21:00 100初仓累计： 100.79411764705884
买入 71.5 2010-01-15 13:59:00 bottom
卖出 74.95 本次获利 3.450000000000003 总获利 3.990000000000009 2010-01-20 11:14:00 100初仓累计： 105.65761003702183
买入 65.22 2010-01-27 14:07:00 bottom
卖出 66.65 本次获利 1.4300000000000068 总获利 5.420000000000016 2010-03-05 10:20:00 100初仓累计： 107.97423656803902
买入 67.39 2010-03-08 11:24:00 bottom
卖出 66.5 本次获利 -0.8900000000000006 总获利 4.530000000000015 2010-03-10 10:19:00 100初仓累计： 106.5482524376702
买入 63.8 2010-03-17 14:40:00 bottom
卖出 62.95 本次获利 -0.8499999999999943 总获利 3.680000000000021 2010-03-25 13:50:00 100初仓累计： 105.12872242870438
买入 69.43 2010-03-30 11:27:00 bottom
卖出 69.48 本次获利 0.04999999999999716 总获利 3.730000000000018 2010-03-31 10:59:00 100初仓累计： 105.20443085620595
买入 69.65 2010-04-01 11:25:00 bottom
卖出 69.27 本次获利 -0.38000000000000966 总获利 3.3500000000000085 2010-04-09 09:41:00 100初仓累计： 104.63045119037164
买入 63.34 2010-04-21 13:13:

卖出 31.7 本次获利 0.7100000000000009 总获利 53.92999999999998 2012-04-16 10:40:00 100初仓累计： 199.32111188412946
买入 31.98 2012-04-18 14:10:00 bottom
卖出 33.1 本次获利 1.120000000000001 总获利 55.04999999999998 2012-04-24 13:46:00 100初仓累计： 206.30171367619403
买入 33.54 2012-04-25 15:00:00 bottom
卖出 33.54 本次获利 0.0 总获利 55.04999999999998 2012-05-09 14:00:00 100初仓累计： 206.30171367619403
买入 31.89 2012-05-17 14:11:00 bottom
卖出 31.53 本次获利 -0.35999999999999943 总获利 54.68999999999998 2012-05-21 13:41:00 100初仓累计： 203.97281380402626
买入 32.23 2012-05-23 09:37:00 bottom
卖出 32.7 本次获利 0.47000000000000597 总获利 55.15999999999999 2012-05-25 13:42:00 100初仓累计： 206.9472854915191
买入 34.32 2012-05-29 13:06:00 bottom
卖出 34.01 本次获利 -0.3100000000000023 总获利 54.84999999999999 2012-05-30 13:11:00 100初仓累计： 205.07800639762715
买入 32.16 2012-06-07 10:56:00 bottom
卖出 31.88 本次获利 -0.2799999999999976 总获利 54.56999999999999 2012-06-12 13:30:00 100初仓累计： 203.29250136680204
买入 31.99 2012-06-13 14:13:00 bottom
卖出 31.86 本次获利 -0.129999999999999 总获利 54.44

卖出 20.82 本次获利 2.1400000000000006 总获利 68.82999999999997 2014-08-06 10:06:00 100初仓累计： 421.05516675726045
买入 21.03 2014-08-12 09:54:00 bottom
卖出 20.92 本次获利 -0.10999999999999943 总获利 68.71999999999997 2014-08-14 14:35:00 100初仓累计： 418.8527859515877
买入 21.05 2014-08-18 14:45:00 bottom
卖出 20.81 本次获利 -0.240000000000002 总获利 68.47999999999996 2014-08-20 11:07:00 100初仓累计： 414.0772672519021
买入 20.44 2014-08-29 10:24:00 bottom
卖出 20.9 本次获利 0.4599999999999973 总获利 68.93999999999996 2014-09-10 10:38:00 100初仓累计： 423.3960315834027
买入 20.15 2014-09-19 10:22:00 bottom
卖出 20.28 本次获利 0.13000000000000256 总获利 69.06999999999996 2014-09-26 14:24:00 100初仓累计： 426.12761888394084
买入 20.38 2014-10-08 14:10:00 bottom
卖出 20.23 本次获利 -0.14999999999999858 总获利 68.91999999999996 2014-10-13 13:27:00 100初仓累计： 422.9912526998098
买入 19.46 2014-10-28 14:31:00 bottom
卖出 20.3 本次获利 0.8399999999999999 总获利 69.75999999999996 2014-11-06 10:32:00 100初仓累计： 441.24986792426205
买入 20.52 2014-11-10 09:54:00 bottom
卖出 20.77 本次获利 0.25 总获利 70.00

卖出 8.85 本次获利 -0.2400000000000002 总获利 82.60999999999996 2016-08-24 09:31:00 100初仓累计： 904.2911180384752
买入 9.03 2016-09-06 14:00:00 bottom
卖出 9.15 本次获利 0.120000000000001 总获利 82.72999999999996 2016-09-08 13:49:00 100初仓累计： 916.3082757532724
买入 8.85 2016-09-14 14:40:00 bottom
卖出 9.01 本次获利 0.16000000000000014 总获利 82.88999999999996 2016-09-27 10:23:00 100初仓累计： 932.8743010776253
买入 9.03 2016-09-30 10:51:00 bottom
卖出 9.22 本次获利 0.19000000000000128 总获利 83.07999999999996 2016-10-13 13:14:00 100初仓累计： 952.5028854856818
买入 9.32 2016-10-24 14:47:00 bottom
卖出 9.63 本次获利 0.3100000000000005 总获利 83.38999999999996 2016-10-31 09:59:00 100初仓累计： 984.1848484149265
买入 9.64 2016-11-01 11:19:00 bottom
卖出 10.05 本次获利 0.41000000000000014 总获利 83.79999999999995 2016-11-04 13:26:00 100初仓累计： 1026.0433326317439
买入 10.08 2016-11-28 10:17:00 bottom
卖出 10.84 本次获利 0.7599999999999998 总获利 84.55999999999996 2016-12-08 14:38:00 100初仓累计： 1103.4037426317561
买入 10.23 2016-12-14 10:49:00 bottom
卖出 10.08 本次获利 -0.15000000000000036 总获利 

卖出 11.62 本次获利 0.6199999999999992 总获利 92.23999999999994 2019-03-22 13:38:00 100初仓累计： 2443.898052275256
买入 11.48 2019-03-27 10:21:00 bottom
卖出 13.43 本次获利 1.9499999999999993 总获利 94.18999999999994 2019-04-11 13:17:00 100初仓累计： 2859.020108193091
买入 13.5 2019-04-12 10:27:00 bottom
卖出 13.71 本次获利 0.21000000000000085 总获利 94.39999999999995 2019-04-18 09:55:00 100初仓累计： 2903.4937543205388
买入 13.66 2019-04-19 13:20:00 bottom
卖出 13.37 本次获利 -0.2900000000000009 总获利 94.10999999999994 2019-04-22 13:18:00 100初仓累计： 2841.8529645143194
买入 12.27 2019-04-29 14:50:00 bottom
卖出 11.4 本次获利 -0.8699999999999992 总获利 93.23999999999994 2019-05-06 11:24:00 100初仓累计： 2640.3523875683163
买入 11.71 2019-05-07 10:43:00 bottom
卖出 11.68 本次获利 -0.030000000000001137 总获利 93.20999999999994 2019-05-09 10:10:00 100初仓累计： 2633.5880347393622
买入 11.68 2019-05-10 11:12:00 bottom
卖出 11.69 本次获利 0.009999999999999787 总获利 93.21999999999994 2019-05-17 13:14:00 100初仓累计： 2635.84281901568
买入 11.25 2019-05-21 10:26:00 bottom
卖出 11.83 本次获利 0.580000000

In [228]:
len(df.loc[(df["line"]=='bottom') | (df["line"]=='top')])

10201

In [215]:
qs_mark_df.loc[0:9]

zsg_dd zsg_dir zsg_end_dir  zsg_gg  \
0   23.61                  up   24.33   
1   24.37      up        down   27.50   
2   24.06    down        down   24.19   
3   21.75    down          up   22.60   
4   20.61    down        down   21.23   
5   19.35    down        down   20.50   
6   17.35    down          up   17.58   
7   18.69      up          up   19.06   
8   19.54      up        down   20.60   
9   12.50    down          up   13.18   

                                             zsg_nos zsg_start_dir  
0                                                 1,            up  
1  2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,18,...            up  
2                                                31,          down  
3                                                31,          down  
4                                                32,          down  
5                                          33,34,35,          down  
6                                                36,          down  
7                                                37,            up  
8                                                38,            up  
9                                          39,40,40,          down

In [70]:
result_df.groupby('direction')['trade_price'].mean()

direction
downdown    13.105517
upup        16.638000
Name: trade_price, dtype: float64

In [255]:
outputpath='E:/jupyter/000425-10Y.csv'
df.to_csv(outputpath,sep=',',index=True,header=True)